# 5D Kerr-AdS spacetime with a Nambu-Goto string

## Case a = b

This [SageMath](https://www.sagemath.org/) notebook is relative to the article *Holographic drag force in 5d Kerr-AdS black hole* by Irina Ya. Aref'eva, Anastasia A. Golubtsova and Eric Gourgoulhon, [arXiv:2004.12984](https://arxiv.org/abs/2004.12984).


The involved differential geometry computations are based on tools developed through the [SageManifolds](https://sagemanifolds.obspm.fr) project.

*NB:* a version of SageMath at least equal to 8.2 is required to run this notebook:

In [1]:
version()

'SageMath version 9.3, Release Date: 2021-05-09'

First we set up the notebook to display mathematical objects using LaTeX rendering:

In [2]:
%display latex

Since some computations are quite long, we ask for running them in parallel on 8 cores:

In [3]:
Parallelism().set(nproc=1)  # only nproc=1 works on CoCalc

## Spacetime manifold

We declare the Kerr-AdS spacetime as a 5-dimensional Lorentzian manifold:

In [4]:
M = Manifold(5, 'M', r'\mathcal{M}', structure='Lorentzian', metric_name='G')
print(M)

5-dimensional Lorentzian manifold M


Let us define **Boyer-Lindquist-type coordinates (rational polynomial version)** on $\mathcal{M}$, via the method `chart()`, the argument of which is a string expressing the coordinates names, their ranges (the default is $(-\infty,+\infty)$) and their LaTeX symbols:

In [5]:
BL.<t,r,mu,ph,ps> = M.chart(r't r:(0,+oo) mu:(0,1):\mu ph:(0,2*pi):\phi ps:(0,2*pi):\psi')
BL

Chart (M, (t, r, mu, ph, ps))

The coordinate $\mu$ is related to the standard Boyer-Lindquist coordinate $\theta$ by
$$ \mu = \cos\theta$$

The coordinate ranges are

In [6]:
BL.coord_range()

t: (-oo, +oo); r: (0, +oo); mu: (0, 1); ph: (0, 2*pi); ps: (0, 2*pi)

Note that contrary to the 4-dimensional case, the range of $\mu$ is $(0,1)$ only (cf. Sec. 1.2 of [R.C. Myers, arXiv:1111.1903](https://arxiv.org/abs/1111.1903) or Sec. 2 of [G.W. Gibbons, H. Lüb, Don N. Page, C.N. Pope, J. Geom. Phys. **53**, 49 (2005)](https://doi.org/10.1016/j.geomphys.2004.05.001)). In other words, the range of $\theta$ is $\left(0, \frac{\pi}{2}\right)$ only. 

## Metric tensor

The 4 parameters $m$, $a$, $b$ and $\ell$ of the Kerr-AdS spacetime are declared as symbolic variables, $a$ and $b$ being the two angular momentum parameters and $\ell$ being related to the cosmological constant by $\Lambda = - 6 \ell^2$:

In [7]:
var('m a b', domain='real')

(m, a, b)

In [8]:
var('l', domain='real', latex_name=r'\ell')

l

In [9]:
# Particular cases
# m = 0
# a = 0
# b = 0
b = a

Some auxiliary functions:

In [10]:
keep_Delta = False  # change to False to provide explicit expression for Delta_r, Xi_a, etc...

In [11]:
sig = (1 + r^2*l^2)/r^2
costh2 = mu^2
sinth2 = 1 - mu^2
rho2 = r^2 + a^2*mu^2 + b^2*sinth2
if keep_Delta:
    Delta_r = var('Delta_r', latex_name=r'\Delta_r', domain='real')
    Delta_th = var('Delta_th', latex_name=r'\Delta_\theta', domain='real')
    if a == b:
        Xi_a = var('Xi', latex_name=r'\Xi', domain='real')
        Xi_b = Xi_a
    else:
        Xi_a = var('Xi_a', latex_name=r'\Xi_a', domain='real')
        Xi_b = var('Xi_b', latex_name=r'\Xi_b', domain='real')
    #Delta_th = 1 - a^2*l^2*mu^2 - b^2*l^2*sinth2
    Xi_a = 1 - a^2*l^2
    Xi_b = 1 - b^2*l^2
else:
    Delta_r = (r^2+a^2)*(r^2+b^2)*sig - 2*m
    Delta_th = 1 - a^2*l^2*mu^2 - b^2*l^2*sinth2
    Xi_a = 1 - a^2*l^2
    Xi_b = 1 - b^2*l^2

The metric is set by its components in the coordinate frame associated with the Boyer-Lindquist-type coordinates, which is the current manifold's default frame. These components can be deduced from
Eq. (5.22) of the article [S.W. Hawking, C.J. Hunter & M.M. Taylor-Robinson, Phys. Rev. D **59**, 064005 (1999)](https://doi.org/10.1103/PhysRevD.59.064005) (the check of agreement with this equation is performed below):

In [12]:
G = M.metric()
tmp = 1/rho2*( -Delta_r + Delta_th*(a^2*sinth2 + b^2*mu^2) + a^2*b^2*sig )
G[0,0] = tmp.simplify_full()
tmp = a*sinth2/(rho2*Xi_a)*( Delta_r - (r^2+a^2)*(Delta_th + b^2*sig) )
G[0,3] = tmp.simplify_full()
tmp = b*mu^2/(rho2*Xi_b)*( Delta_r - (r^2+b^2)*(Delta_th + a^2*sig) )
G[0,4] = tmp.simplify_full()
G[1,1] = (rho2/Delta_r).simplify_full()
G[2,2] = (rho2/Delta_th/(1-mu^2)).simplify_full()
tmp = sinth2/(rho2*Xi_a^2)*( - Delta_r*a^2*sinth2 + (r^2+a^2)^2*(Delta_th + sig*b^2*sinth2) ) 
G[3,3] = tmp.simplify_full()
tmp = a*b*sinth2*mu^2/(rho2*Xi_a*Xi_b)*( - Delta_r + sig*(r^2+a^2)*(r^2+b^2) )
G[3,4] = tmp.simplify_full()
tmp = mu^2/(rho2*Xi_b^2)*( - Delta_r*b^2*mu^2 + (r^2+b^2)^2*(Delta_th + sig*a^2*mu^2) )
G[4,4] = tmp.simplify_full()
G.display()

G = -(a^4*l^2 + l^2*r^4 + (2*a^2*l^2 + 1)*r^2 + a^2 - 2*m)/(a^2 + r^2) dt*dt - (a^5*l^2 - (a*l^2*mu^2 - a*l^2)*r^4 - (a^5*l^2 - 2*a*m)*mu^2 - 2*(a^3*l^2*mu^2 - a^3*l^2)*r^2 - 2*a*m)/(a^4*l^2 + (a^2*l^2 - 1)*r^2 - a^2) dt*dph - (2*a^3*l^2*mu^2*r^2 + a*l^2*mu^2*r^4 + (a^5*l^2 - 2*a*m)*mu^2)/(a^4*l^2 + (a^2*l^2 - 1)*r^2 - a^2) dt*dps + (a^2*r^2 + r^4)/(l^2*r^6 + (2*a^2*l^2 + 1)*r^4 + a^4 + (a^4*l^2 + 2*a^2 - 2*m)*r^2) dr*dr - (a^2 + r^2)/(a^2*l^2 - (a^2*l^2 - 1)*mu^2 - 1) dmu*dmu - (a^5*l^2 - (a*l^2*mu^2 - a*l^2)*r^4 - (a^5*l^2 - 2*a*m)*mu^2 - 2*(a^3*l^2*mu^2 - a^3*l^2)*r^2 - 2*a*m)/(a^4*l^2 + (a^2*l^2 - 1)*r^2 - a^2) dph*dt - (a^6*l^2 - 2*a^2*m*mu^4 + (a^2*l^2 - (a^2*l^2 - 1)*mu^2 - 1)*r^4 - a^4 - 2*a^2*m - (a^6*l^2 - a^4 - 4*a^2*m)*mu^2 + 2*(a^4*l^2 - (a^4*l^2 - a^2)*mu^2 - a^2)*r^2)/(a^6*l^4 - 2*a^4*l^2 + (a^4*l^4 - 2*a^2*l^2 + 1)*r^2 + a^2) dph*dph - 2*(a^2*m*mu^4 - a^2*m*mu^2)/(a^6*l^4 - 2*a^4*l^2 + (a^4*l^4 - 2*a^2*l^2 + 1)*r^2 + a^2) dph*dps - (2*a^3*l^2*mu^2*r^2 + a*l^2*mu^2*r^4 + (a^5*l^2 - 2*a*m)*mu^2)/(a^4*l^2 + (a^2*l^2 - 1)*r^2 - a^2) dps*dt - 2*(a^2*m*mu^4 - a^2*m*mu^2)/(a^6*l^4 - 2*a^4*l^2 + (a^4*l^4 - 2*a^2*l^2 + 1)*r^2 + a^2) dps*dph + (2*a^2*m*mu^4 - (a^2*l^2 - 1)*mu^2*r^4 - 2*(a^4*l^2 - a^2)*mu^2*r^2 - (a^6*l^2 - a^4)*mu^2)/(a^6*l^4 - 2*a^4*l^2 + (a^4*l^4 - 2*a^2*l^2 + 1)*r^2 + a^2) dps*dps

In [13]:
G.display_comp(only_nonredundant=True)

G_t,t = -(a^4*l^2 + l^2*r^4 + (2*a^2*l^2 + 1)*r^2 + a^2 - 2*m)/(a^2 + r^2) 
G_t,ph = -(a^5*l^2 - (a*l^2*mu^2 - a*l^2)*r^4 - (a^5*l^2 - 2*a*m)*mu^2 - 2*(a^3*l^2*mu^2 - a^3*l^2)*r^2 - 2*a*m)/(a^4*l^2 + (a^2*l^2 - 1)*r^2 - a^2) 
G_t,ps = -(2*a^3*l^2*mu^2*r^2 + a*l^2*mu^2*r^4 + (a^5*l^2 - 2*a*m)*mu^2)/(a^4*l^2 + (a^2*l^2 - 1)*r^2 - a^2) 
G_r,r = (a^2*r^2 + r^4)/(l^2*r^6 + (2*a^2*l^2 + 1)*r^4 + a^4 + (a^4*l^2 + 2*a^2 - 2*m)*r^2) 
G_mu,mu = -(a^2 + r^2)/(a^2*l^2 - (a^2*l^2 - 1)*mu^2 - 1) 
G_ph,ph = -(a^6*l^2 - 2*a^2*m*mu^4 + (a^2*l^2 - (a^2*l^2 - 1)*mu^2 - 1)*r^4 - a^4 - 2*a^2*m - (a^6*l^2 - a^4 - 4*a^2*m)*mu^2 + 2*(a^4*l^2 - (a^4*l^2 - a^2)*mu^2 - a^2)*r^2)/(a^6*l^4 - 2*a^4*l^2 + (a^4*l^4 - 2*a^2*l^2 + 1)*r^2 + a^2) 
G_ph,ps = -2*(a^2*m*mu^4 - a^2*m*mu^2)/(a^6*l^4 - 2*a^4*l^2 + (a^4*l^4 - 2*a^2*l^2 + 1)*r^2 + a^2) 
G_ps,ps = (2*a^2*m*mu^4 - (a^2*l^2 - 1)*mu^2*r^4 - 2*(a^4*l^2 - a^2)*mu^2*r^2 - (a^6*l^2 - a^4)*mu^2)/(a^6*l^4 - 2*a^4*l^2 + (a^4*l^4 - 2*a^2*l^2 + 1)*r^2 + a^2)

### Check of agreement with Eq. (5.22) of Hawking et al or Eq. (2.3) of our paper

We need the 1-forms $\mathrm{d}t$, $\mathrm{d}r$, $\mathrm{d}\mu$, $\mathrm{d}\phi$ and $\mathrm{d}\psi$:

In [14]:
dt, dr, dmu, dph, dps = (BL.coframe()[i] for i in M.irange())
dt, dr, dmu, dph, dps

(1-form dt on the 5-dimensional Lorentzian manifold M,
 1-form dr on the 5-dimensional Lorentzian manifold M,
 1-form dmu on the 5-dimensional Lorentzian manifold M,
 1-form dph on the 5-dimensional Lorentzian manifold M,
 1-form dps on the 5-dimensional Lorentzian manifold M)

In [15]:
print(dt)

1-form dt on the 5-dimensional Lorentzian manifold M


In agreement with $\mu = \cos\theta$, we introduce the 1-form $\mathrm{d}\theta = - \mathrm{d}\mu /\sin\theta $, with 
$\sin\theta = \sqrt{1-\mu^2}$ since $\theta\in\left(0, \frac{\pi}{2}\right)$:

In [16]:
dth = - 1/sqrt(1 - mu^2)*dmu

In [17]:
s1 = dt - a*sinth2/Xi_a*dph - b*costh2/Xi_b*dps
s1.display()

dt - (a*mu^2 - a)/(a^2*l^2 - 1) dph + a*mu^2/(a^2*l^2 - 1) dps

In [18]:
s2 = a*dt - (r^2 + a^2)/Xi_a*dph
s2.display()

a dt + (a^2 + r^2)/(a^2*l^2 - 1) dph

In [19]:
s3 = b*dt - (r^2 + b^2)/Xi_b*dps
s3.display()

a dt + (a^2 + r^2)/(a^2*l^2 - 1) dps

In [20]:
s4 = a*b*dt - b*(r^2 + a^2)*sinth2/Xi_a * dph - a*(r^2 + b^2)*costh2/Xi_b * dps
s4.display()

a^2 dt - (a^3*mu^2 - a^3 + (a*mu^2 - a)*r^2)/(a^2*l^2 - 1) dph + (a^3*mu^2 + a*mu^2*r^2)/(a^2*l^2 - 1) dps

In [21]:
G0 = - Delta_r/rho2 * s1*s1 + Delta_th*sinth2/rho2 * s2*s2 + Delta_th*costh2/rho2 * s3*s3 \
     + rho2/Delta_r * dr*dr + rho2/Delta_th * dth*dth + sig/rho2 * s4*s4
G0.display_comp(only_nonredundant=True)

X_t,t = -(a^4*l^2 + l^2*r^4 + (2*a^2*l^2 + 1)*r^2 + a^2 - 2*m)/(a^2 + r^2) 
X_t,ph = -(a^5*l^2 - (a*l^2*mu^2 - a*l^2)*r^4 - (a^5*l^2 - 2*a*m)*mu^2 - 2*(a^3*l^2*mu^2 - a^3*l^2)*r^2 - 2*a*m)/(a^4*l^2 + (a^2*l^2 - 1)*r^2 - a^2) 
X_t,ps = -(2*a^3*l^2*mu^2*r^2 + a*l^2*mu^2*r^4 + (a^5*l^2 - 2*a*m)*mu^2)/(a^4*l^2 + (a^2*l^2 - 1)*r^2 - a^2) 
X_r,r = -(a^2*mu^2 - (mu^2 - 1)*a^2 + r^2)/(2*m - (l^2*r^2 + 1)*(a^2 + r^2)^2/r^2) 
X_mu,mu = -(a^2 + r^2)/(a^2*l^2 - (a^2*l^2 - 1)*mu^2 - 1) 
X_ph,t = -(a^5*l^2 - (a*l^2*mu^2 - a*l^2)*r^4 - (a^5*l^2 - 2*a*m)*mu^2 - 2*(a^3*l^2*mu^2 - a^3*l^2)*r^2 - 2*a*m)/(a^4*l^2 + (a^2*l^2 - 1)*r^2 - a^2) 
X_ph,ph = -(a^6*l^2 - 2*a^2*m*mu^4 + (a^2*l^2 - (a^2*l^2 - 1)*mu^2 - 1)*r^4 - a^4 - 2*a^2*m - (a^6*l^2 - a^4 - 4*a^2*m)*mu^2 + 2*(a^4*l^2 - (a^4*l^2 - a^2)*mu^2 - a^2)*r^2)/(a^6*l^4 - 2*a^4*l^2 + (a^4*l^4 - 2*a^2*l^2 + 1)*r^2 + a^2) 
X_ph,ps = -2*(a^2*m*mu^4 - a^2*m*mu^2)/(a^6*l^4 - 2*a^4*l^2 + (a^4*l^4 - 2*a^2*l^2 + 1)*r^2 + a^2) 
X_ps,t = -(2*a^3*l^2*mu^2*r^2 + a*l^2*mu^2*r^4 + (a^5*l^2 - 2*a*m)*mu^2)/(a^4*l^2 + (a^2*l^2 - 1)*r^2 - a^2) 
X_ps,ph = -2*(a^2*m*mu^4 - a^2*m*mu^2)/(a^6*l^4 - 2*a^4*l^2 + (a^4*l^4 - 2*a^2*l^2 + 1)*r^2 + a^2) 
X_ps,ps = (2*a^2*m*mu^4 - (a^2*l^2 - 1)*mu^2*r^4 - 2*(a^4*l^2 - a^2)*mu^2*r^2 - (a^6*l^2 - a^4)*mu^2)/(a^6*l^4 - 2*a^4*l^2 + (a^4*l^4 - 2*a^2*l^2 + 1)*r^2 + a^2)

In [22]:
G0 == G

True

## Einstein equation

The Ricci tensor of $g$ is

In [23]:
if not keep_Delta:
    # Ric = G.ricci()
    # print(Ric)
    pass

In [24]:
if not keep_Delta:
    # show(Ric.display_comp(only_nonredundant=True))
    pass

Let us check that $g$ is a solution of the vacuum Einstein equation with the cosmological constant $\Lambda = - 6 \ell^2$:

In [25]:
Lambda = -6*l^2
if not keep_Delta:
    # print(Ric == 2/3*Lambda*G)
    pass

### Check of Eq. (2.10)

One must have $a=b$ and `keep_Delta == False` for the test to pass:

In [26]:
if a == b and not keep_Delta:
    G1 = - (1 + rho2*l^2 - 2*m/rho2) * dt*dt + rho2/Delta_r * dr*dr \
         + rho2/Delta_th * dth*dth \
         + sinth2/Xi_a^2*(rho2*Xi_a + 2*a^2*m/rho2*sinth2) * dph * dph \
         + costh2/Xi_a^2*(rho2*Xi_a + 2*a^2*m/rho2*costh2) * dps * dps \
         + a*sinth2/Xi_a*(rho2*l^2 - 2*m/rho2) * (dt*dph + dph*dt) \
         + a*costh2/Xi_a*(rho2*l^2 - 2*m/rho2) * (dt*dps + dps*dt) \
         + 2*m*a^2*sinth2*costh2/Xi_a^2/rho2 * (dph*dps + dps*dph)
    print(G1 == G)

True


## String worldsheet

The string worldsheet as a 2-dimensional Lorentzian manifold:

In [27]:
W = Manifold(2, 'W', structure='Lorentzian')
print(W)

2-dimensional Lorentzian manifold W


Let us assume that the string worldsheet is parametrized by $(t,r)$:

In [28]:
XW.<t,r> = W.chart(r't r:(0,+oo)')
XW

Chart (W, (t, r))

The string embedding in Kerr-AdS spacetime, as an expansion about a 
straight string solution in AdS (Eq. (4.6)-(4.8) of the paper):

In [29]:
Mu0 = var('Mu0', latex_name=r'\mu_0', domain='real')
Phi0 = var('Phi0', latex_name=r'\Phi_0', domain='real')
Psi0 = var('Psi0', latex_name=r'\Psi_0', domain='real')
beta1 = var('beta1', latex_name=r'\beta_1', domain='real')
beta2 = var('beta2', latex_name=r'\beta_2', domain='real')

cosTh0 = Mu0
sinTh0 = sqrt(1 - Mu0^2)

mu_s = Mu0 + a^2*function('mu_1')(r)
ph_s = Phi0 + beta1*a*l^2*t + beta1*a*function('phi_1')(r)
ps_s = Psi0 + beta2*a*l^2*t + beta2*a*function('psi_1')(r)

F = W.diff_map(M, {(XW, BL): [t, r, mu_s, ph_s, ps_s]}, name='F') 
F.display()

F: W --> M
   (t, r) |--> (t, r, mu, ph, ps) = (t, r, a^2*mu_1(r) + Mu0, a*beta1*l^2*t + a*beta1*phi_1(r) + Phi0, a*beta2*l^2*t + a*beta2*psi_1(r) + Psi0)

In [30]:
F.jacobian_matrix()

[                        1                         0]
[                        0                         1]
[                        0      a^2*diff(mu_1(r), r)]
[              a*beta1*l^2 a*beta1*diff(phi_1(r), r)]
[              a*beta2*l^2 a*beta2*diff(psi_1(r), r)]

### Induced metric on the string worldsheet

The string worldsheet metric is the metric $g$ induced by the spacetime metric $G$, i.e. the pullback of $G$ by the embedding $F$:

In [31]:
g = W.metric()
g.set(F.pullback(G))

In [32]:
# g[0,0].expr().factor()

## Nambu-Goto action

In [33]:
detg = g.determinant().expr()

Expanding at second order in $a$:

In [34]:
detg_a2 = detg.series(a, 3).truncate().simplify_full()
detg_a2 

(((Mu0^2*a^2*beta2^2 - (Mu0^2 - 1)*a^2*beta1^2 + 2*Mu0^2*a^2*beta2 - 2*(Mu0^2 - 1)*a^2*beta1)*l^4 - l^2)*r^4 + ((Mu0^2 - 1)*a^2*beta1^2*l^4*r^8 + 2*(Mu0^2 - 1)*a^2*beta1^2*l^2*r^6 - 4*(Mu0^2 - 1)*a^2*beta1^2*m*r^2 + 4*(Mu0^2 - 1)*a^2*beta1^2*m^2 - (4*(Mu0^2 - 1)*a^2*beta1^2*l^2*m - (Mu0^2 - 1)*a^2*beta1^2)*r^4)*diff(phi_1(r), r)^2 - (Mu0^2*a^2*beta2^2*l^4*r^8 + 2*Mu0^2*a^2*beta2^2*l^2*r^6 - 4*Mu0^2*a^2*beta2^2*m*r^2 + 4*Mu0^2*a^2*beta2^2*m^2 - (4*Mu0^2*a^2*beta2^2*l^2*m - Mu0^2*a^2*beta2^2)*r^4)*diff(psi_1(r), r)^2 + a^2 - 2*(2*(Mu0^2*a^2*beta2 - (Mu0^2 - 1)*a^2*beta1)*l^2 - 1)*m - r^2)/(l^2*r^4 + r^2 - 2*m)

The Nambu-Goto Lagrangian at second order in $a$:

In [35]:
L_a2 = (sqrt(-detg_a2)).series(a, 3).truncate().simplify_full()
L_a2

-1/2*(((Mu0^2*a^2*beta2^2 - (Mu0^2 - 1)*a^2*beta1^2 + 2*Mu0^2*a^2*beta2 - 2*(Mu0^2 - 1)*a^2*beta1)*l^4 - 2*l^2)*r^4 + ((Mu0^2 - 1)*a^2*beta1^2*l^4*r^8 + 2*(Mu0^2 - 1)*a^2*beta1^2*l^2*r^6 - 4*(Mu0^2 - 1)*a^2*beta1^2*m*r^2 + 4*(Mu0^2 - 1)*a^2*beta1^2*m^2 - (4*(Mu0^2 - 1)*a^2*beta1^2*l^2*m - (Mu0^2 - 1)*a^2*beta1^2)*r^4)*diff(phi_1(r), r)^2 - (Mu0^2*a^2*beta2^2*l^4*r^8 + 2*Mu0^2*a^2*beta2^2*l^2*r^6 - 4*Mu0^2*a^2*beta2^2*m*r^2 + 4*Mu0^2*a^2*beta2^2*m^2 - (4*Mu0^2*a^2*beta2^2*l^2*m - Mu0^2*a^2*beta2^2)*r^4)*diff(psi_1(r), r)^2 + a^2 - 4*((Mu0^2*a^2*beta2 - (Mu0^2 - 1)*a^2*beta1)*l^2 - 1)*m - 2*r^2)/(l^2*r^4 + r^2 - 2*m)

In [36]:
L_a2.numerator()

-Mu0^2*a^2*beta1^2*l^4*r^8*diff(phi_1(r), r)^2 + Mu0^2*a^2*beta2^2*l^4*r^8*diff(psi_1(r), r)^2 + a^2*beta1^2*l^4*r^8*diff(phi_1(r), r)^2 - 2*Mu0^2*a^2*beta1^2*l^2*r^6*diff(phi_1(r), r)^2 + 2*Mu0^2*a^2*beta2^2*l^2*r^6*diff(psi_1(r), r)^2 + 4*Mu0^2*a^2*beta1^2*l^2*m*r^4*diff(phi_1(r), r)^2 - 4*Mu0^2*a^2*beta2^2*l^2*m*r^4*diff(psi_1(r), r)^2 + Mu0^2*a^2*beta1^2*l^4*r^4 - Mu0^2*a^2*beta2^2*l^4*r^4 + 2*a^2*beta1^2*l^2*r^6*diff(phi_1(r), r)^2 + 2*Mu0^2*a^2*beta1*l^4*r^4 - 2*Mu0^2*a^2*beta2*l^4*r^4 - 4*a^2*beta1^2*l^2*m*r^4*diff(phi_1(r), r)^2 - a^2*beta1^2*l^4*r^4 - Mu0^2*a^2*beta1^2*r^4*diff(phi_1(r), r)^2 + Mu0^2*a^2*beta2^2*r^4*diff(psi_1(r), r)^2 - 2*a^2*beta1*l^4*r^4 + 4*Mu0^2*a^2*beta1^2*m*r^2*diff(phi_1(r), r)^2 - 4*Mu0^2*a^2*beta2^2*m*r^2*diff(psi_1(r), r)^2 - 4*Mu0^2*a^2*beta1^2*m^2*diff(phi_1(r), r)^2 + a^2*beta1^2*r^4*diff(phi_1(r), r)^2 + 4*Mu0^2*a^2*beta2^2*m^2*diff(psi_1(r), r)^2 - 4*a^2*beta1^2*m*r^2*diff(phi_1(r), r)^2 - 4*Mu0^2*a^2*beta1*l^2*m + 4*Mu0^2*a^2*beta2*l^2*m + 4*a^2*beta1^2*m^2*diff(phi_1(r), r)^2 + 4*a^2*beta1*l^2*m + 2*l^2*r^4 - a^2 + 2*r^2 - 4*m

In [37]:
L_a2.denominator()

2*l^2*r^4 + 2*r^2 - 4*m

###  Euler-Lagrange equations

In [38]:
def euler_lagrange(lagr, qs, var):
    r"""
    Derive the Euler-Lagrange equations from a given Lagrangian.

    INPUT:

    - ``lagr`` -- symbolic expression representing the Lagrangian density
    - ``qs`` -- either a single symbolic function or a list/tuple of
      symbolic functions, representing the `q`'s; these functions must
      appear in ``lagr`` up to at most their first derivatives
    - ``var`` -- either a single variable, typically `t` (1-dimensional
      problem) or a list/tuple of symbolic variables

    OUTPUT:

    - list of Euler-Lagrange equations; if only one function is involved, the
      single Euler-Lagrannge equation is returned instead.

    """
    if not isinstance(qs, (list, tuple)):
        qs = [qs]
    if not isinstance(var, (list, tuple)):
        var = [var]
    n = len(qs)
    d = len(var)
    qv = [SR.var('qxxxx{}'.format(q)) for q in qs]
    dqv = [[SR.var('qxxxx{}_{}'.format(q, v)) for v in var] for q in qs]
    subs = {qs[i](*var): qv[i] for i in range(n)}
    subs_inv = {qv[i]: qs[i](*var) for i in range(n)}
    for i in range(n):
        subs.update({diff(qs[i](*var), var[j]): dqv[i][j]
                     for j in range(d)})
        subs_inv.update({dqv[i][j]: diff(qs[i](*var), var[j])
                         for j in range(d)})
    lg = lagr.substitute(subs)
    eqs = []
    for i in range(n):
        dLdq = diff(lg, qv[i]).simplify_full()
        dLdq = dLdq.substitute(subs_inv)
        ddL = 0
        for j in range(d):
            h =  diff(lg, dqv[i][j]).simplify_full()
            h = h.substitute(subs_inv)
            ddL += diff(h, var[j])
        eqs.append((dLdq - ddL).simplify_full() == 0)
    if n == 1:
        return eqs[0]
    return eqs

We compute the Euler-Lagrange equations at order $a^2$ for $\phi_1$ and $\psi_1$:

In [39]:
eqs = euler_lagrange(L_a2, [phi_1, psi_1], r)
eqs

[2*(2*(Mu0^2 - 1)*a^2*beta1^2*l^2*r^3 + (Mu0^2 - 1)*a^2*beta1^2*r)*diff(phi_1(r), r) + ((Mu0^2 - 1)*a^2*beta1^2*l^2*r^4 + (Mu0^2 - 1)*a^2*beta1^2*r^2 - 2*(Mu0^2 - 1)*a^2*beta1^2*m)*diff(phi_1(r), r, r) == 0,
 -2*(2*Mu0^2*a^2*beta2^2*l^2*r^3 + Mu0^2*a^2*beta2^2*r)*diff(psi_1(r), r) - (Mu0^2*a^2*beta2^2*l^2*r^4 + Mu0^2*a^2*beta2^2*r^2 - 2*Mu0^2*a^2*beta2^2*m)*diff(psi_1(r), r, r) == 0]

#### Solving the equation for $\phi_1$ (Eq. (4.10))

In [40]:
eq_phi1 = eqs[0]
eq_phi1

2*(2*(Mu0^2 - 1)*a^2*beta1^2*l^2*r^3 + (Mu0^2 - 1)*a^2*beta1^2*r)*diff(phi_1(r), r) + ((Mu0^2 - 1)*a^2*beta1^2*l^2*r^4 + (Mu0^2 - 1)*a^2*beta1^2*r^2 - 2*(Mu0^2 - 1)*a^2*beta1^2*m)*diff(phi_1(r), r, r) == 0

In [41]:
eq_phi1 = (eq_phi1/(a^2*(Mu0^2-1)*beta1^2)).simplify_full()
eq_phi1

2*(2*l^2*r^3 + r)*diff(phi_1(r), r) + (l^2*r^4 + r^2 - 2*m)*diff(phi_1(r), r, r) == 0

In [42]:
phi1_sol(r) = desolve(eq_phi1, phi_1(r), ivar=r)
phi1_sol(r)

_K1*integrate(1/(l^2*r^4 + r^2 - 2*m), r) + _K2

We revover Eqs. (4.10) with $K_1 = \mathcal{P}/\beta_1^2$ and $K_2=0$.
In what follows, we introduce $\mathcal{P}' = \mathcal{P}/\beta_1^2$ instead of $\mathcal{P}$.

The symbolic constants $K_1$ and $K_2$ are actually denoted `_K1` and `_K2` by SageMath, as the `print` reveals:

In [43]:
print(phi1_sol(r))

_K1*integrate(1/(l^2*r^4 + r^2 - 2*m), r) + _K2


Hence we perform the substitutions with `SR.var('_K1')` and `SR.var('_K2')`:

In [44]:
P = var("P", latex_name=r"\mathcal{P}'")
phi1_sol(r) = phi1_sol(r).subs({SR.var('_K1'): P, SR.var('_K2'): 0})
print(phi1_sol(r))

P*integrate(1/(l^2*r^4 + r^2 - 2*m), r)


#### Solving the equation for $\psi_1$  (Eq. (4.10))

In [45]:
eq_psi1 = eqs[1]
eq_psi1

-2*(2*Mu0^2*a^2*beta2^2*l^2*r^3 + Mu0^2*a^2*beta2^2*r)*diff(psi_1(r), r) - (Mu0^2*a^2*beta2^2*l^2*r^4 + Mu0^2*a^2*beta2^2*r^2 - 2*Mu0^2*a^2*beta2^2*m)*diff(psi_1(r), r, r) == 0

In [46]:
eq_psi1 = (eq_psi1/(a^2*Mu0^2*beta2^2)).simplify_full()
eq_psi1

-2*(2*l^2*r^3 + r)*diff(psi_1(r), r) - (l^2*r^4 + r^2 - 2*m)*diff(psi_1(r), r, r) == 0

In [47]:
psi1_sol(r) = desolve(eq_psi1, psi_1(r), ivar=r)
psi1_sol(r)

_K1*integrate(1/(l^2*r^4 + r^2 - 2*m), r) + _K2

We revover Eq. (4.10) with $K_1 = \mathcal{Q}/\beta_2^2$ and $K_2=0$.
In what follows, we introduce $\mathcal{Q}' = \mathcal{Q}/\beta_2^2$ instead of $\mathcal{Q}$:

In [48]:
Q = var('Q', latex_name=r"\mathcal{Q}'")
psi1_sol(r) = psi1_sol(r).subs({SR.var('_K1'): Q, SR.var('_K2'): 0})
print(psi1_sol(r))

Q*integrate(1/(l^2*r^4 + r^2 - 2*m), r)


### Nambu-Goto Lagrangian at fourth order in $a$

In [49]:
detg_a4 = detg.series(a, 5).truncate().simplify_full()

In [50]:
L_a4 = (sqrt(-detg_a4)).series(a, 5).truncate().simplify_full()

In [51]:
eqs = euler_lagrange(L_a4, [phi_1, psi_1, mu_1], r)

### The equation for $\mu_1$

In [52]:
eq_mu1 = eqs[2]
eq_mu1

(((Mu0^3 - Mu0)*a^4*beta1^2 - (Mu0^3 - Mu0)*a^4*beta2^2 + 2*(Mu0^3 - Mu0)*a^4*beta1 - 2*(Mu0^3 - Mu0)*a^4*beta2)*l^4*r^4 - 4*((Mu0^3 - Mu0)*a^4*beta1 - (Mu0^3 - Mu0)*a^4*beta2)*l^2*m - ((Mu0^3 - Mu0)*a^4*beta1^2*l^4*r^8 + 2*(Mu0^3 - Mu0)*a^4*beta1^2*l^2*r^6 - 4*(Mu0^3 - Mu0)*a^4*beta1^2*m*r^2 + 4*(Mu0^3 - Mu0)*a^4*beta1^2*m^2 - (4*(Mu0^3 - Mu0)*a^4*beta1^2*l^2*m - (Mu0^3 - Mu0)*a^4*beta1^2)*r^4)*diff(phi_1(r), r)^2 + ((Mu0^3 - Mu0)*a^4*beta2^2*l^4*r^8 + 2*(Mu0^3 - Mu0)*a^4*beta2^2*l^2*r^6 - 4*(Mu0^3 - Mu0)*a^4*beta2^2*m*r^2 + 4*(Mu0^3 - Mu0)*a^4*beta2^2*m^2 - (4*(Mu0^3 - Mu0)*a^4*beta2^2*l^2*m - (Mu0^3 - Mu0)*a^4*beta2^2)*r^4)*diff(psi_1(r), r)^2 + 2*(2*a^4*l^4*r^7 + 3*a^4*l^2*r^5 - 2*a^4*m*r - (4*a^4*l^2*m - a^4)*r^3)*diff(mu_1(r), r) + (a^4*l^4*r^8 + 2*a^4*l^2*r^6 - 4*a^4*m*r^2 + 4*a^4*m^2 - (4*a^4*l^2*m - a^4)*r^4)*diff(mu_1(r), r, r))/((Mu0^2 - 1)*l^2*r^4 + (Mu0^2 - 1)*r^2 - 2*(Mu0^2 - 1)*m) == 0

In [53]:
# eq_mu1.lhs().numerator().simplify_full()

In [54]:
eq_mu1.lhs().denominator().simplify_full()

(Mu0^2 - 1)*l^2*r^4 + (Mu0^2 - 1)*r^2 - 2*(Mu0^2 - 1)*m

In [55]:
eq_mu1 = eq_mu1.lhs().numerator().simplify_full() == 0
#eq_mu1

In [56]:
eq_mu1 = (eq_mu1/a^4).simplify_full()
eq_mu1

((Mu0^3 - Mu0)*beta1^2 - (Mu0^3 - Mu0)*beta2^2 + 2*(Mu0^3 - Mu0)*beta1 - 2*(Mu0^3 - Mu0)*beta2)*l^4*r^4 - 4*((Mu0^3 - Mu0)*beta1 - (Mu0^3 - Mu0)*beta2)*l^2*m - ((Mu0^3 - Mu0)*beta1^2*l^4*r^8 + 2*(Mu0^3 - Mu0)*beta1^2*l^2*r^6 - 4*(Mu0^3 - Mu0)*beta1^2*m*r^2 + 4*(Mu0^3 - Mu0)*beta1^2*m^2 - (4*(Mu0^3 - Mu0)*beta1^2*l^2*m - (Mu0^3 - Mu0)*beta1^2)*r^4)*diff(phi_1(r), r)^2 + ((Mu0^3 - Mu0)*beta2^2*l^4*r^8 + 2*(Mu0^3 - Mu0)*beta2^2*l^2*r^6 - 4*(Mu0^3 - Mu0)*beta2^2*m*r^2 + 4*(Mu0^3 - Mu0)*beta2^2*m^2 - (4*(Mu0^3 - Mu0)*beta2^2*l^2*m - (Mu0^3 - Mu0)*beta2^2)*r^4)*diff(psi_1(r), r)^2 + 2*(2*l^4*r^7 + 3*l^2*r^5 - (4*l^2*m - 1)*r^3 - 2*m*r)*diff(mu_1(r), r) + (l^4*r^8 + 2*l^2*r^6 - (4*l^2*m - 1)*r^4 - 4*m*r^2 + 4*m^2)*diff(mu_1(r), r, r) == 0

We plug the solutions obtained previously for $\phi_1(r)$ and $\psi_1(r)$ in this equation:

In [57]:
eq_mu1 = eq_mu1.substitute_function(phi_1, phi1_sol).substitute_function(psi_1, psi1_sol)
eq_mu1 = eq_mu1.simplify_full()
eq_mu1

((Mu0^3 - Mu0)*beta1^2 - (Mu0^3 - Mu0)*beta2^2 + 2*(Mu0^3 - Mu0)*beta1 - 2*(Mu0^3 - Mu0)*beta2)*l^4*r^4 - (Mu0^3 - Mu0)*P^2*beta1^2 + (Mu0^3 - Mu0)*Q^2*beta2^2 - 4*((Mu0^3 - Mu0)*beta1 - (Mu0^3 - Mu0)*beta2)*l^2*m + 2*(2*l^4*r^7 + 3*l^2*r^5 - (4*l^2*m - 1)*r^3 - 2*m*r)*diff(mu_1(r), r) + (l^4*r^8 + 2*l^2*r^6 - (4*l^2*m - 1)*r^4 - 4*m*r^2 + 4*m^2)*diff(mu_1(r), r, r) == 0

### Check of Eq. (4.11)

In [58]:
lhs = eq_mu1.lhs()
lhs = lhs.simplify_full()
lhs

((Mu0^3 - Mu0)*beta1^2 - (Mu0^3 - Mu0)*beta2^2 + 2*(Mu0^3 - Mu0)*beta1 - 2*(Mu0^3 - Mu0)*beta2)*l^4*r^4 - (Mu0^3 - Mu0)*P^2*beta1^2 + (Mu0^3 - Mu0)*Q^2*beta2^2 - 4*((Mu0^3 - Mu0)*beta1 - (Mu0^3 - Mu0)*beta2)*l^2*m + 2*(2*l^4*r^7 + 3*l^2*r^5 - (4*l^2*m - 1)*r^3 - 2*m*r)*diff(mu_1(r), r) + (l^4*r^8 + 2*l^2*r^6 - (4*l^2*m - 1)*r^4 - 4*m*r^2 + 4*m^2)*diff(mu_1(r), r, r)

In [59]:
s = lhs.coefficient(diff(mu_1(r), r, 2))  # coefficient of mu_1''
s.factor()

(l^2*r^4 + r^2 - 2*m)^2

In [60]:
s1 = (lhs/s - diff(mu_1(r), r, 2)).simplify_full()
s1

(((Mu0^3 - Mu0)*beta1^2 - (Mu0^3 - Mu0)*beta2^2 + 2*(Mu0^3 - Mu0)*beta1 - 2*(Mu0^3 - Mu0)*beta2)*l^4*r^4 - (Mu0^3 - Mu0)*P^2*beta1^2 + (Mu0^3 - Mu0)*Q^2*beta2^2 - 4*((Mu0^3 - Mu0)*beta1 - (Mu0^3 - Mu0)*beta2)*l^2*m + 2*(2*l^4*r^7 + 3*l^2*r^5 - (4*l^2*m - 1)*r^3 - 2*m*r)*diff(mu_1(r), r))/(l^4*r^8 + 2*l^2*r^6 - (4*l^2*m - 1)*r^4 - 4*m*r^2 + 4*m^2)

In [61]:
b1 = s1.coefficient(diff(mu_1(r), r)).factor()
b1

2*(2*l^2*r^2 + 1)*r/(l^2*r^4 + r^2 - 2*m)

In [62]:
s2 = (s1 - b1*diff(mu_1(r), r)).simplify_full()
s2

(((Mu0^3 - Mu0)*beta1^2 - (Mu0^3 - Mu0)*beta2^2 + 2*(Mu0^3 - Mu0)*beta1 - 2*(Mu0^3 - Mu0)*beta2)*l^4*r^4 - (Mu0^3 - Mu0)*P^2*beta1^2 + (Mu0^3 - Mu0)*Q^2*beta2^2 - 4*((Mu0^3 - Mu0)*beta1 - (Mu0^3 - Mu0)*beta2)*l^2*m)/(l^4*r^8 + 2*l^2*r^6 - (4*l^2*m - 1)*r^4 - 4*m*r^2 + 4*m^2)

In [63]:
s2.factor()

(beta1^2*l^4*r^4 - beta2^2*l^4*r^4 + 2*beta1*l^4*r^4 - 2*beta2*l^4*r^4 - P^2*beta1^2 + Q^2*beta2^2 - 4*beta1*l^2*m + 4*beta2*l^2*m)*(Mu0 + 1)*(Mu0 - 1)*Mu0/(l^2*r^4 + r^2 - 2*m)^2

The equation for $\mu_1$ is thus:

In [64]:
eq_mu1 = diff(mu_1(r), r, 2) + b1*diff(mu_1(r), r) + s2.factor() == 0
eq_mu1

(beta1^2*l^4*r^4 - beta2^2*l^4*r^4 + 2*beta1*l^4*r^4 - 2*beta2*l^4*r^4 - P^2*beta1^2 + Q^2*beta2^2 - 4*beta1*l^2*m + 4*beta2*l^2*m)*(Mu0 + 1)*(Mu0 - 1)*Mu0/(l^2*r^4 + r^2 - 2*m)^2 + 2*(2*l^2*r^2 + 1)*r*diff(mu_1(r), r)/(l^2*r^4 + r^2 - 2*m) + diff(mu_1(r), r, r) == 0

In [65]:
h(r) = l^2 + 1/r^2 - 2*m/r^4
h(r)

l^2 + 1/r^2 - 2*m/r^4

In [66]:
s3 = (s2 / (Mu0*(1-Mu0^2))* r^8*h(r)^2).simplify_full()
s3

-(beta1^2 - beta2^2 + 2*beta1 - 2*beta2)*l^4*r^4 + P^2*beta1^2 - Q^2*beta2^2 + 4*(beta1 - beta2)*l^2*m

Given that 
$$ \mu_1(r) = - \sin\Theta_0 \; \theta_1(r) = - \sqrt{1-\mu_0^2}  \; \theta_1(r), \qquad \sin2\Theta_0 = 2\mu_0\sqrt{1-\mu_0^2}$$
and
$$\mathcal{P}' = \mathcal{P}/\beta_1^2 \qquad\mbox{and}\qquad \mathcal{Q}' = \mathcal{Q}/\beta_1^2,$$ 
we get for the equation for $\theta_1$:
$$ \theta_1'' + \frac{2r(2\ell^2 r^2 + 1)}{r^4 h} \, \theta_1' + \frac{\beta_2^{-2}\mathcal{Q}^2 - \beta_1^{-2}\mathcal{P}^2 - 4 (\beta_1 - \beta_2) \ell^2 m + (\beta_1^2 - \beta_2^2 + 2 (\beta_1 - \beta_2)) \ell^4 r^4}{2 r^8 h^2}\sin(2\Theta_0) = 0 $$ 

This agrees with Eq. (4.11) of the paper.

### Solving the equation for $\mu_1$

In [67]:
mu1_sol(r) = desolve(eq_mu1, mu_1(r), ivar=r)
mu1_sol(r)

_K2 - integrate((((Mu0^3 - Mu0)*beta1^2 - (Mu0^3 - Mu0)*beta2^2 + 2*(Mu0^3 - Mu0)*beta1 - 2*(Mu0^3 - Mu0)*beta2)*l^2*r + (Mu0^3 - Mu0)*integrate(-((beta1^2 - beta2^2 + 2*beta1 - 2*beta2)*l^2*r^2 + P^2*beta1^2 - Q^2*beta2^2 - 2*(beta1^2 - beta2^2)*l^2*m)/(l^2*r^4 + r^2 - 2*m), r) - _K1)/(l^2*r^4 + r^2 - 2*m), r)

In [68]:
print(mu1_sol(r))

_K2 - integrate((((Mu0^3 - Mu0)*beta1^2 - (Mu0^3 - Mu0)*beta2^2 + 2*(Mu0^3 - Mu0)*beta1 - 2*(Mu0^3 - Mu0)*beta2)*l^2*r + (Mu0^3 - Mu0)*integrate(-((beta1^2 - beta2^2 + 2*beta1 - 2*beta2)*l^2*r^2 + P^2*beta1^2 - Q^2*beta2^2 - 2*(beta1^2 - beta2^2)*l^2*m)/(l^2*r^4 + r^2 - 2*m), r) - _K1)/(l^2*r^4 + r^2 - 2*m), r)


Let us check that `mu1_sol` is indeed a solution of the equation for $\mu_1$:

In [69]:
eq_mu1.substitute_function(mu_1, mu1_sol).simplify_full()

0 == 0

In [70]:
mu1_sol(r)

_K2 - integrate((((Mu0^3 - Mu0)*beta1^2 - (Mu0^3 - Mu0)*beta2^2 + 2*(Mu0^3 - Mu0)*beta1 - 2*(Mu0^3 - Mu0)*beta2)*l^2*r + (Mu0^3 - Mu0)*integrate(-((beta1^2 - beta2^2 + 2*beta1 - 2*beta2)*l^2*r^2 + P^2*beta1^2 - Q^2*beta2^2 - 2*(beta1^2 - beta2^2)*l^2*m)/(l^2*r^4 + r^2 - 2*m), r) - _K1)/(l^2*r^4 + r^2 - 2*m), r)

The innermost integral can be written
$$ (\beta_1^2 - \beta_2^2 + 2 (\beta_1-\beta_2)) \ell^2 \; s_1(r) + \left({\mathcal{P}'}^2 \beta_1^2 - {\mathcal{Q}'}\beta_2^2 - 2 (\beta_1^2-\beta_2^2)\ell^2 m \right) \; s_2(r)$$
with 
$$ s_1(r) := \int^r \frac{\bar{r}^2}{\ell^2 \bar{r}^4 + \bar{r}^2 - 2m} \, \mathrm{d}\bar{r} \qquad \mbox{and}\qquad s_2(r) := \int^r \frac{\mathrm{d}\bar{r}}{\ell^2 \bar{r}^4 + \bar{r}^2 - 2m} .$$

Let us evaluate $s_1$ by means of FriCAS:

In [71]:
s1 = integrate(r^2/(l^2*r^4 + r^2 - 2*m), r, algorithm='fricas')
s1

1/2*sqrt(1/2)*sqrt(-((8*l^4*m + l^2)/sqrt(8*l^6*m + l^4) + 1)/(8*l^4*m + l^2))*log(sqrt(1/2)*(8*l^4*m + l^2)*sqrt(-((8*l^4*m + l^2)/sqrt(8*l^6*m + l^4) + 1)/(8*l^4*m + l^2))/sqrt(8*l^6*m + l^4) + r) - 1/2*sqrt(1/2)*sqrt(-((8*l^4*m + l^2)/sqrt(8*l^6*m + l^4) + 1)/(8*l^4*m + l^2))*log(-sqrt(1/2)*(8*l^4*m + l^2)*sqrt(-((8*l^4*m + l^2)/sqrt(8*l^6*m + l^4) + 1)/(8*l^4*m + l^2))/sqrt(8*l^6*m + l^4) + r) - 1/2*sqrt(1/2)*sqrt(((8*l^4*m + l^2)/sqrt(8*l^6*m + l^4) - 1)/(8*l^4*m + l^2))*log(sqrt(1/2)*(8*l^4*m + l^2)*sqrt(((8*l^4*m + l^2)/sqrt(8*l^6*m + l^4) - 1)/(8*l^4*m + l^2))/sqrt(8*l^6*m + l^4) + r) + 1/2*sqrt(1/2)*sqrt(((8*l^4*m + l^2)/sqrt(8*l^6*m + l^4) - 1)/(8*l^4*m + l^2))*log(-sqrt(1/2)*(8*l^4*m + l^2)*sqrt(((8*l^4*m + l^2)/sqrt(8*l^6*m + l^4) - 1)/(8*l^4*m + l^2))/sqrt(8*l^6*m + l^4) + r)

In [72]:
s1 = s1.canonicalize_radical().simplify_log()
s1

1/4*(sqrt(2)*sqrt(8*l^2*m - sqrt(8*l^2*m + 1) + 1)*log((sqrt(2)*(8*l^2*m + 1)^(1/4)*l*r - sqrt(8*l^2*m - sqrt(8*l^2*m + 1) + 1))/(sqrt(2)*(8*l^2*m + 1)^(1/4)*l*r + sqrt(8*l^2*m - sqrt(8*l^2*m + 1) + 1))) + sqrt(2)*sqrt(-8*l^2*m - sqrt(8*l^2*m + 1) - 1)*log((sqrt(2)*(8*l^2*m + 1)^(1/4)*l*r + sqrt(-8*l^2*m - sqrt(8*l^2*m + 1) - 1))/(sqrt(2)*(8*l^2*m + 1)^(1/4)*l*r - sqrt(-8*l^2*m - sqrt(8*l^2*m + 1) - 1))))/((8*l^2*m + 1)^(3/4)*l)

Check:

In [73]:
diff(s1, r).simplify_full()

r^2/(l^2*r^4 + r^2 - 2*m)

Similarly, we evaluate $s_2$ by means of FriCAS:

In [74]:
s2 = integrate(1/(l^2*r^4 + r^2 - 2*m), r, algorithm='fricas')
s2

-1/4*sqrt(((8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) + 1)/(8*l^2*m^2 + m))*log(2*l^2*r + 1/2*(8*l^2*m - (8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) + 1)*sqrt(((8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) + 1)/(8*l^2*m^2 + m))) + 1/4*sqrt(((8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) + 1)/(8*l^2*m^2 + m))*log(2*l^2*r - 1/2*(8*l^2*m - (8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) + 1)*sqrt(((8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) + 1)/(8*l^2*m^2 + m))) - 1/4*sqrt(-((8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) - 1)/(8*l^2*m^2 + m))*log(2*l^2*r + 1/2*(8*l^2*m + (8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) + 1)*sqrt(-((8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) - 1)/(8*l^2*m^2 + m))) + 1/4*sqrt(-((8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) - 1)/(8*l^2*m^2 + m))*log(2*l^2*r - 1/2*(8*l^2*m + (8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) + 1)*sqrt(-((8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) - 1)/(8*l^2*m^2 + m)))

In [75]:
s2 = s2.canonicalize_radical().simplify_log()
s2

1/4*(sqrt(-8*l^2*m + sqrt(8*l^2*m + 1) - 1)*log((4*(8*l^2*m + 1)^(1/4)*l^2*sqrt(m)*r - sqrt(-8*l^2*m + sqrt(8*l^2*m + 1) - 1)*(sqrt(8*l^2*m + 1) + 1))/(4*(8*l^2*m + 1)^(1/4)*l^2*sqrt(m)*r + sqrt(-8*l^2*m + sqrt(8*l^2*m + 1) - 1)*(sqrt(8*l^2*m + 1) + 1))) + sqrt(8*l^2*m + sqrt(8*l^2*m + 1) + 1)*log((4*(8*l^2*m + 1)^(1/4)*l^2*sqrt(m)*r - sqrt(8*l^2*m + sqrt(8*l^2*m + 1) + 1)*(sqrt(8*l^2*m + 1) - 1))/(4*(8*l^2*m + 1)^(1/4)*l^2*sqrt(m)*r + sqrt(8*l^2*m + sqrt(8*l^2*m + 1) + 1)*(sqrt(8*l^2*m + 1) - 1))))/((8*l^2*m + 1)^(3/4)*sqrt(m))

Check:

In [76]:
diff(s2, r).simplify_full()

1/(l^2*r^4 + r^2 - 2*m)

In the above expressions for $s_1(r)$ and $s_2(r)$ there appears the factor 
$$\mathfrak{P} = \sqrt{1 + 8\ell^2 m},$$
which we represent by the symbolic variable `B`

In [77]:
B = var('B')
assume(B > 1)

Let us make $B$ appear in $s_1$:

In [78]:
s1 = s1.subs({l^2: (B^2 - 1)/(8*m)}).simplify_full()
s1

1/4*(sqrt(2)*sqrt(B^2 - B)*log((sqrt(2)*sqrt(B)*l*r - sqrt(B^2 - B))/(sqrt(2)*sqrt(B)*l*r + sqrt(B^2 - B))) + sqrt(2)*sqrt(-B^2 - B)*log((sqrt(2)*sqrt(B)*l*r + sqrt(-B^2 - B))/(sqrt(2)*sqrt(B)*l*r - sqrt(-B^2 - B))))/(B^(3/2)*l)

In this expression, there appears the term $\sqrt{-B^2-B}$ which is imaginary since $B>1$. 
We there rewrite it as $i\sqrt{B}\sqrt{B+1}$:

In [79]:
s1 = s1.subs({sqrt(-B^2 - B): I*sqrt(B)*sqrt(B + 1), 
              sqrt(B^2 - B): sqrt(B)*sqrt(B - 1)})
s1

1/4*(I*sqrt(2)*sqrt(B + 1)*sqrt(B)*log((sqrt(2)*sqrt(B)*l*r + I*sqrt(B + 1)*sqrt(B))/(sqrt(2)*sqrt(B)*l*r - I*sqrt(B + 1)*sqrt(B))) + sqrt(2)*sqrt(B - 1)*sqrt(B)*log((sqrt(2)*sqrt(B)*l*r - sqrt(B - 1)*sqrt(B))/(sqrt(2)*sqrt(B)*l*r + sqrt(B - 1)*sqrt(B))))/(B^(3/2)*l)

In [80]:
s1 = s1.simplify_log()
s1

1/4*(I*sqrt(2)*sqrt(B + 1)*log((sqrt(2)*l*r + I*sqrt(B + 1))/(sqrt(2)*l*r - I*sqrt(B + 1))) + sqrt(2)*sqrt(B - 1)*log((sqrt(2)*l*r - sqrt(B - 1))/(sqrt(2)*l*r + sqrt(B - 1))))/(B*l)

In the first $\log$, we recognize the $\mathrm{arctan}$ function, via the identity
$$
    \mathrm{arctan}\,  x = \frac{i}{2} \ln\left( \frac{i + x}{i - x} \right), 
$$
which we use in the form
$$
i \ln\left( \frac{x + i}{x - i} \right) = 2 \mathrm{arctan}(x) - \pi
$$
as we can check:

In [81]:
taylor(I*ln((x+I)/(x-I)) - 2*atan(x) + pi, x, 0, 10)

0

Thus, we set, disregarding the additive constant $-\pi$,

In [82]:
s1 = sqrt(2)/(4*B*l)*(2*sqrt(B+1)*atan(sqrt(2)*l/sqrt(B+1)*r)
                      + sqrt(B-1)*ln((sqrt(2)*l/sqrt(B-1)*r - 1)/(sqrt(2)*l/sqrt(B-1)*r + 1)))
s1

1/4*sqrt(2)*(2*sqrt(B + 1)*arctan(sqrt(2)*l*r/sqrt(B + 1)) + sqrt(B - 1)*log((sqrt(2)*l*r/sqrt(B - 1) - 1)/(sqrt(2)*l*r/sqrt(B - 1) + 1)))/(B*l)

Let us check that we have indeed a primitive of $r\mapsto \frac{r^2}{\ell^2 r^4 + r^2 - 2m}$:

In [83]:
Ds1 = diff(s1, r).simplify_full()
Ds1

4*l^2*r^2/(4*l^4*r^4 + 4*l^2*r^2 - B^2 + 1)

In [84]:
Ds1.subs({B: sqrt(1 + 8*l^2*m)}).simplify_full()

r^2/(l^2*r^4 + r^2 - 2*m)

Similarly, we can express $s_2$ in terms of $B$:

In [85]:
s2 = s2.subs({l^2: (B^2 - 1)/(8*m)}).simplify_full()
s2

1/4*(sqrt(B^2 + B)*log(((B + 1)*sqrt(B)*sqrt(m)*r - 2*sqrt(B^2 + B)*m)/((B + 1)*sqrt(B)*sqrt(m)*r + 2*sqrt(B^2 + B)*m)) + sqrt(-B^2 + B)*log(((B - 1)*sqrt(B)*sqrt(m)*r - 2*sqrt(-B^2 + B)*m)/((B - 1)*sqrt(B)*sqrt(m)*r + 2*sqrt(-B^2 + B)*m)))/(B^(3/2)*sqrt(m))

Since $B>1$, we replace $\sqrt{-B^2 + B}$ by $i\sqrt{B}\sqrt{B-1}$:

In [86]:
s2 = s2.subs({sqrt(-B^2 + B): I*sqrt(B)*sqrt(B - 1), 
              sqrt(B^2 + B): sqrt(B)*sqrt(B + 1)})
s2

1/4*(sqrt(B + 1)*sqrt(B)*log(((B + 1)*sqrt(B)*sqrt(m)*r - 2*sqrt(B + 1)*sqrt(B)*m)/((B + 1)*sqrt(B)*sqrt(m)*r + 2*sqrt(B + 1)*sqrt(B)*m)) + I*sqrt(B - 1)*sqrt(B)*log(((B - 1)*sqrt(B)*sqrt(m)*r - 2*I*sqrt(B - 1)*sqrt(B)*m)/((B - 1)*sqrt(B)*sqrt(m)*r + 2*I*sqrt(B - 1)*sqrt(B)*m)))/(B^(3/2)*sqrt(m))

In [87]:
s2 = s2.simplify_log()
s2

1/4*(sqrt(B + 1)*log(((B + 1)*sqrt(m)*r - 2*sqrt(B + 1)*m)/((B + 1)*sqrt(m)*r + 2*sqrt(B + 1)*m)) + I*sqrt(B - 1)*log(((B - 1)*sqrt(m)*r - 2*I*sqrt(B - 1)*m)/((B - 1)*sqrt(m)*r + 2*I*sqrt(B - 1)*m)))/(B*sqrt(m))

Again, we use the identity
$$
i \ln\left( \frac{x + i}{x - i} \right) = 2 \mathrm{arctan}(x) - \pi
$$
to rewrite $s_2$ as

In [88]:
s2 = 1/(4*B*sqrt(m))*(sqrt(B+1)*ln( (sqrt(B+1)/(2*sqrt(m))*r - 1)
                                   /(sqrt(B+1)/(2*sqrt(m))*r + 1) )
                      - 2*sqrt(B-1)*atan(sqrt(B-1)/(2*sqrt(m))*r))
s2

-1/4*(2*sqrt(B - 1)*arctan(1/2*sqrt(B - 1)*r/sqrt(m)) - sqrt(B + 1)*log((sqrt(B + 1)*r/sqrt(m) - 2)/(sqrt(B + 1)*r/sqrt(m) + 2)))/(B*sqrt(m))

Let us check that we have indeed a primitive of $r\mapsto \frac{1}{\ell^2 r^4 + r^2 - 2m}$:

In [89]:
Ds2 = diff(s2, r).simplify_full()
Ds2

8*m/((B^2 - 1)*r^4 + 8*m*r^2 - 16*m^2)

In [90]:
Ds2.subs({B: sqrt(1 + 8*l^2*m)}).simplify_full()

1/(l^2*r^4 + r^2 - 2*m)

Given the above expressions for $s_1(r)$ and $s_2(r)$ we rewrite the solution

In [91]:
mu1_sol(r)

_K2 - integrate((((Mu0^3 - Mu0)*beta1^2 - (Mu0^3 - Mu0)*beta2^2 + 2*(Mu0^3 - Mu0)*beta1 - 2*(Mu0^3 - Mu0)*beta2)*l^2*r + (Mu0^3 - Mu0)*integrate(-((beta1^2 - beta2^2 + 2*beta1 - 2*beta2)*l^2*r^2 + P^2*beta1^2 - Q^2*beta2^2 - 2*(beta1^2 - beta2^2)*l^2*m)/(l^2*r^4 + r^2 - 2*m), r) - _K1)/(l^2*r^4 + r^2 - 2*m), r)

as 

Instead of $K_1$ and $K_2$, let us introduce the constants $C_1$ and $C_2$:

In [92]:
C1, C2 = var('C_1', 'C_2') 

In [93]:
# mu1 / mu0(1-mu0^2) : 
mu1s0 = -C2/(Mu0*sqrt(1-Mu0^2)) - C1/(Mu0*sqrt(1-Mu0^2))*s2 \
        + integrate(((beta1^2 - beta2^2 + 2*(beta1 - beta2))*l^2*r 
                     - (beta1^2 - beta2^2 +2*(beta1-beta2))*l^2 * s1
              - (P^2*beta1^2 - Q^2*beta2^2 - 2*(beta1^2 - beta2^2)*l^2*m) * s2)
                     / (l^2*r^4 + r^2 - 2*m), 
                    r, hold=True)
mu1s0

-C_2/(sqrt(-Mu0^2 + 1)*Mu0) + 1/4*(2*sqrt(B - 1)*arctan(1/2*sqrt(B - 1)*r/sqrt(m)) - sqrt(B + 1)*log((sqrt(B + 1)*r/sqrt(m) - 2)/(sqrt(B + 1)*r/sqrt(m) + 2)))*C_1/(sqrt(-Mu0^2 + 1)*B*Mu0*sqrt(m)) + integrate(1/4*(4*(beta1^2 - beta2^2 + 2*beta1 - 2*beta2)*l^2*r - sqrt(2)*(beta1^2 - beta2^2 + 2*beta1 - 2*beta2)*(2*sqrt(B + 1)*arctan(sqrt(2)*l*r/sqrt(B + 1)) + sqrt(B - 1)*log((sqrt(2)*l*r/sqrt(B - 1) - 1)/(sqrt(2)*l*r/sqrt(B - 1) + 1)))*l/B + (P^2*beta1^2 - Q^2*beta2^2 - 2*(beta1^2 - beta2^2)*l^2*m)*(2*sqrt(B - 1)*arctan(1/2*sqrt(B - 1)*r/sqrt(m)) - sqrt(B + 1)*log((sqrt(B + 1)*r/sqrt(m) - 2)/(sqrt(B + 1)*r/sqrt(m) + 2)))/(B*sqrt(m)))/(l^2*r^4 + r^2 - 2*m), r)

In [94]:
mu1_sol(r) = mu1s0 * Mu0*(1-Mu0^2)
mu1_sol(r)

1/4*(Mu0^2 - 1)*Mu0*(4*C_2/(sqrt(-Mu0^2 + 1)*Mu0) - (2*sqrt(B - 1)*arctan(1/2*sqrt(B - 1)*r/sqrt(m)) - sqrt(B + 1)*log((sqrt(B + 1)*r/sqrt(m) - 2)/(sqrt(B + 1)*r/sqrt(m) + 2)))*C_1/(sqrt(-Mu0^2 + 1)*B*Mu0*sqrt(m)) - 4*integrate(1/4*(4*(beta1^2 - beta2^2 + 2*beta1 - 2*beta2)*l^2*r - sqrt(2)*(beta1^2 - beta2^2 + 2*beta1 - 2*beta2)*(2*sqrt(B + 1)*arctan(sqrt(2)*l*r/sqrt(B + 1)) + sqrt(B - 1)*log((sqrt(2)*l*r/sqrt(B - 1) - 1)/(sqrt(2)*l*r/sqrt(B - 1) + 1)))*l/B + (P^2*beta1^2 - Q^2*beta2^2 - 2*(beta1^2 - beta2^2)*l^2*m)*(2*sqrt(B - 1)*arctan(1/2*sqrt(B - 1)*r/sqrt(m)) - sqrt(B + 1)*log((sqrt(B + 1)*r/sqrt(m) - 2)/(sqrt(B + 1)*r/sqrt(m) + 2)))/(B*sqrt(m)))/(l^2*r^4 + r^2 - 2*m), r))

Let us check that we do have a solution of the equation for $\mu_1$:

In [95]:
eq_mu1.substitute_function(mu_1, mu1_sol).simplify_full().subs({B: sqrt(1 + 8*l^2*m)}).simplify_full()

0 == 0

### Conjugate momenta

In [96]:
def conjugate_momenta(lagr, qs, var):
    r"""
    Compute the conjugate momenta from a given Lagrangian.

    INPUT:

    - ``lagr`` -- symbolic expression representing the Lagrangian density
    - ``qs`` -- either a single symbolic function or a list/tuple of
      symbolic functions, representing the `q`'s; these functions must
      appear in ``lagr`` up to at most their first derivatives
    - ``var`` -- either a single variable, typically `t` (1-dimensional
      problem) or a list/tuple of symbolic variables; in the latter case the
      time coordinate must the first one

    OUTPUT:

    - list of conjugate momenta; if only one function is involved, the
      single conjugate momentum is returned instead.

    """
    if not isinstance(qs, (list, tuple)):
        qs = [qs]
    if not isinstance(var, (list, tuple)):
        var = [var]
    n = len(qs)
    d = len(var)
    dqvt = [SR.var('qxxxx{}_t'.format(q)) for q in qs]
    subs = {diff(qs[i](*var), var[0]): dqvt[i] for i in range(n)}
    subs_inv = {dqvt[i]: diff(qs[i](*var), var[0]) for i in range(n)}
    lg = lagr.substitute(subs)
    ps = [diff(lg, dotq).simplify_full().substitute(subs_inv) for dotq in dqvt]
    if n == 1:
        return ps[0]
    return ps

In [97]:
pis = conjugate_momenta(L_a2, [phi_1, psi_1], r)
pis

[-(Mu0^2 - 1)*a^2*beta1^2*l^2*r^4*diff(phi_1(r), r) - (Mu0^2 - 1)*a^2*beta1^2*r^2*diff(phi_1(r), r) + 2*(Mu0^2 - 1)*a^2*beta1^2*m*diff(phi_1(r), r),
 Mu0^2*a^2*beta2^2*l^2*r^4*diff(psi_1(r), r) + Mu0^2*a^2*beta2^2*r^2*diff(psi_1(r), r) - 2*Mu0^2*a^2*beta2^2*m*diff(psi_1(r), r)]

### Check of Eq. (4.14):

In [98]:
pi_phi_r = (pis[0]/(a*beta1)).substitute_function(phi_1, phi1_sol).simplify_full()
pi_phi_r

-(Mu0^2 - 1)*P*a*beta1

### Check of Eq. (4.15):

In [99]:
pi_psi_r = (pis[1]/(a*beta2)).substitute_function(psi_1, psi1_sol).simplify_full()
pi_psi_r

Mu0^2*Q*a*beta2

### Check of Eq. (4.13):

In [100]:
pis4 = conjugate_momenta(L_a4, [phi_1, psi_1, mu_1], r)

In [101]:
pis4[2]

-(a^4*l^2*r^4*diff(mu_1(r), r) + a^4*r^2*diff(mu_1(r), r) - 2*a^4*m*diff(mu_1(r), r))/(Mu0^2 - 1)

The quantity $\pi_\theta^r / (a^2 \sin\Theta_0\cos\Theta_0)$:

In [102]:
pi_theta_r_a2sT0 = (- pis4[2] / (a^4*Mu0)).substitute_function(mu_1, mu1_sol).simplify_full()
pi_theta_r_a2sT0 = pi_theta_r_a2sT0.subs({B: sqrt(1 + 8*l^2*m)}).simplify_full()
pi_theta_r_a2sT0

1/4*((2*(sqrt(2)*Mu0*beta1^2 - sqrt(2)*Mu0*beta2^2 + 2*sqrt(2)*Mu0*beta1 - 2*sqrt(2)*Mu0*beta2)*l*sqrt(m)*arctan(sqrt(2)*l*r/sqrt(sqrt(8*l^2*m + 1) + 1)) + (Mu0*P^2*beta1^2 - Mu0*Q^2*beta2^2 - 2*(Mu0*beta1^2 - Mu0*beta2^2)*l^2*m)*log((sqrt(m)*r*sqrt(sqrt(8*l^2*m + 1) + 1) - 2*m)/(sqrt(m)*r*sqrt(sqrt(8*l^2*m + 1) + 1) + 2*m)))*sqrt(-Mu0^2 + 1)*sqrt(sqrt(8*l^2*m + 1) + 1) + ((sqrt(2)*Mu0*beta1^2 - sqrt(2)*Mu0*beta2^2 + 2*sqrt(2)*Mu0*beta1 - 2*sqrt(2)*Mu0*beta2)*l*sqrt(m)*log((sqrt(2)*l*r*sqrt(sqrt(8*l^2*m + 1) - 1) - sqrt(8*l^2*m + 1) + 1)/(sqrt(2)*l*r*sqrt(sqrt(8*l^2*m + 1) - 1) + sqrt(8*l^2*m + 1) - 1)) - 2*(Mu0*P^2*beta1^2 - Mu0*Q^2*beta2^2 - 2*(Mu0*beta1^2 - Mu0*beta2^2)*l^2*m)*arctan(1/2*r*sqrt(sqrt(8*l^2*m + 1) - 1)/sqrt(m)))*sqrt(-Mu0^2 + 1)*sqrt(sqrt(8*l^2*m + 1) - 1) - 4*((Mu0*beta1^2 - Mu0*beta2^2 + 2*Mu0*beta1 - 2*Mu0*beta2)*sqrt(-Mu0^2 + 1)*l^2*sqrt(m)*r - C_1*sqrt(m))*sqrt(8*l^2*m + 1))/(sqrt(8*l^2*m + 1)*sqrt(-Mu0^2 + 1)*Mu0*sqrt(m))

The quantity 
$$\frac{\pi_\theta^r}{(a^2/2) \sin 2\Theta_0} + (\beta_1^2 - \beta_2^2 + 2 (\beta_1-\beta_2))\ell^2 r - \frac{C_1}{\sin\Theta_0\cos\Theta_0}$$

In [103]:
part1 = - (beta1^2 - beta2^2 + 2*(beta1-beta2))*l^2*r + C1/(Mu0*sqrt(1-Mu0^2))
s = (pi_theta_r_a2sT0  - part1).simplify_full()
s

1/4*((2*(sqrt(2)*beta1^2 - sqrt(2)*beta2^2 + 2*sqrt(2)*beta1 - 2*sqrt(2)*beta2)*l*sqrt(m)*arctan(sqrt(2)*l*r/sqrt(sqrt(8*l^2*m + 1) + 1)) + (P^2*beta1^2 - Q^2*beta2^2 - 2*(beta1^2 - beta2^2)*l^2*m)*log((sqrt(m)*r*sqrt(sqrt(8*l^2*m + 1) + 1) - 2*m)/(sqrt(m)*r*sqrt(sqrt(8*l^2*m + 1) + 1) + 2*m)))*sqrt(sqrt(8*l^2*m + 1) + 1) + ((sqrt(2)*beta1^2 - sqrt(2)*beta2^2 + 2*sqrt(2)*beta1 - 2*sqrt(2)*beta2)*l*sqrt(m)*log((sqrt(2)*l*r*sqrt(sqrt(8*l^2*m + 1) - 1) - sqrt(8*l^2*m + 1) + 1)/(sqrt(2)*l*r*sqrt(sqrt(8*l^2*m + 1) - 1) + sqrt(8*l^2*m + 1) - 1)) - 2*(P^2*beta1^2 - Q^2*beta2^2 - 2*(beta1^2 - beta2^2)*l^2*m)*arctan(1/2*r*sqrt(sqrt(8*l^2*m + 1) - 1)/sqrt(m)))*sqrt(sqrt(8*l^2*m + 1) - 1))/(sqrt(8*l^2*m + 1)*sqrt(m))

Let us perform an expansion in $1/r$ for $r\rightarrow +\infty$:

In [104]:
u = var('u')
assume(u > 0)
s = s.subs({r: 1/u}).simplify_log()
assume(l>0)
s = s.taylor(u, 0, 2)
s = s.subs({u: 1/r})
s

1/4*((sqrt(2)*pi*beta1^2 - sqrt(2)*pi*beta2^2 + 2*sqrt(2)*pi*beta1 - 2*sqrt(2)*pi*beta2)*l*sqrt(m)*sqrt(sqrt(8*l^2*m + 1) + 1) - (pi*P^2*beta1^2 - pi*Q^2*beta2^2 - 2*(pi*beta1^2 - pi*beta2^2)*l^2*m)*sqrt(sqrt(8*l^2*m + 1) - 1))/(sqrt(8*l^2*m + 1)*sqrt(m)) - (beta1^2 - beta2^2 + 2*beta1 - 2*beta2)/r

In [105]:
s

1/4*((sqrt(2)*pi*beta1^2 - sqrt(2)*pi*beta2^2 + 2*sqrt(2)*pi*beta1 - 2*sqrt(2)*pi*beta2)*l*sqrt(m)*sqrt(sqrt(8*l^2*m + 1) + 1) - (pi*P^2*beta1^2 - pi*Q^2*beta2^2 - 2*(pi*beta1^2 - pi*beta2^2)*l^2*m)*sqrt(sqrt(8*l^2*m + 1) - 1))/(sqrt(8*l^2*m + 1)*sqrt(m)) - (beta1^2 - beta2^2 + 2*beta1 - 2*beta2)/r

Final result for $\frac{\pi_\theta^r}{(a^2/2) \sin 2\Theta_0}$:

In [106]:
part1 + s

-(beta1^2 - beta2^2 + 2*beta1 - 2*beta2)*l^2*r + 1/4*((sqrt(2)*pi*beta1^2 - sqrt(2)*pi*beta2^2 + 2*sqrt(2)*pi*beta1 - 2*sqrt(2)*pi*beta2)*l*sqrt(m)*sqrt(sqrt(8*l^2*m + 1) + 1) - (pi*P^2*beta1^2 - pi*Q^2*beta2^2 - 2*(pi*beta1^2 - pi*beta2^2)*l^2*m)*sqrt(sqrt(8*l^2*m + 1) - 1))/(sqrt(8*l^2*m + 1)*sqrt(m)) - (beta1^2 - beta2^2 + 2*beta1 - 2*beta2)/r + C_1/(sqrt(-Mu0^2 + 1)*Mu0)

The terms in $r$, $1/r$ and $C_1$ agree with Eq. (4.13).